![](https://github.com/bigdata-icict/ETL-Dataiku-DSS/raw/master/tutoriais/pcdas_1.5.png)

# Notebook para criação de tabela de indicadores da PNS -  módulo U 2013 Saúde Bucal

## Bibliotecas Utilizadas

In [178]:
#Lendo pacotes necessários
library(survey)
library(ggplot2)
library(dplyr)
library(tictoc)
library(foreign)
library(forcats)
library(tidyverse)

## Carregando microdados da PNS

In [179]:
#Carregando banco de dados para R versão 3.5.0 ou superior
load("<coloque aqui o caminho para o arquivo dos microdados formato RDATA PNS 2013>")

#conferindo as dimensões (número de linhas e colunas)
dim("<Coloque aqui o nome do arquivo RDATA PNS 2013>")

[1] 222385   1000

## Definição do peso e filtragem de respondentes do questionário

In [180]:
#Selecionando registros válidos para o módulo P e calculando peso amostral - summary de verificação
pns2013.1<- <Coloque aqui o nome do arquivo RDATA> %>% filter(M001==1) 
pns2013.1<-pns2013.1 %>% mutate(peso_morador_selec=((V00291*(60202/145572211))))
pns2013.1<-pns2013.1 %>% filter(!is.na(peso_morador_selec))
summary(pns2013.1$peso_morador_selec)

     Min.   1st Qu.    Median      Mean   3rd Qu.      Max. 
 0.004156  0.243959  0.521557  1.000000  1.147413 31.179597 

## Criação de variáveis dos indicadores

In [181]:
#Escovação dos dentes pelo menos duas vezes por dia - U001P
pns2013.1 <- pns2013.1 %>% mutate(U001P = if_else(U001==4,1,2,missing=2))
pns2013.1$U001P<-factor(pns2013.1$U001P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2013.1$U001P)

#Uso de escova de dente, pasta de dente e fio dental para a limpeza dos dentes - U002P
pns2013.1 <- pns2013.1 %>% mutate(U002P = if_else(U00201==1 & U00202==1 & U00203==1,1,2,missing=2))
pns2013.1$U002P<-factor(pns2013.1$U002P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2013.1$U002P)

#Saúde bucal boa ou muito boa - U003P
pns2013.1 <- pns2013.1 %>% mutate(U003P = if_else(U005==1 | U005==2,1,2,missing=2))
pns2013.1$U003P<-factor(pns2013.1$U003P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2013.1$U003P)

#Perda de todos os dentes - U004P
pns2013.1 <- pns2013.1 %>% mutate(U004P = if_else(U023==3 & U024==3,1,2,missing=2))
pns2013.1$U004P<-factor(pns2013.1$U004P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2013.1$U004P)

#Perda de 13 ou mais dentes -U005P
pns2013.1 <- pns2013.1 %>% mutate(DP = U02301 + U02401)
pns2013.1 <- pns2013.1 %>% mutate(U005P = if_else(DP>=13 | U023==3 | U024==3,1,2,missing=2))
pns2013.1$U005P<-factor(pns2013.1$U005P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2013.1$U005P)

#Consulta odontológica realizada pelo SUS - U006P
pns2013.1 <- pns2013.1 %>% mutate(U006P = if_else(U021==1,1,2))
pns2013.1$U006P<-factor(pns2013.1$U006P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2013.1$U006P)

Sim   Não 
53594  6608

Sim   Não 
30685 29517

Sim   Não 
39572 20630

Sim   Não 
 6606 53596

Sim   Não 
14271 45931

Sim   Não  NA's 
 6451 19205 34546

## Definições de abrangências

### Situação urbana ou rural

In [182]:
#Situação Urbano ou Rural
pns2013.1 <- pns2013.1 %>% rename(Sit_Urbano_Rural=V0026)
pns2013.1$Sit_Urbano_Rural<-factor(pns2013.1$Sit_Urbano_Rural, levels=c(1,2), labels=c("urbano", "rural"))
summary(pns2013.1$Sit_Urbano_Rural)

urbano  rural 
 49245  10957

### Sexo

In [183]:
#Sexo
pns2013.1 <- pns2013.1 %>% rename(Sexo=C006)
pns2013.1$Sexo<-factor(pns2013.1$Sexo, levels=c(1,2), labels=c("Masculino", "Feminino"))
summary(pns2013.1$Sexo)

Masculino  Feminino 
    25920     34282

### UF

In [184]:
#Estados - UFs
pns2013.1 <- pns2013.1 %>% rename(Unidades_da_Federacao=V0001)
pns2013.1$Unidades_da_Federacao<-factor(pns2013.1$Unidades_da_Federacao, levels=c(11,12,13,14,15,16,17,21,22,23,24,25,26,27,28,29,31,32,33,35,41,42,43,50,51,52,53),
                                       label=c("Rondônia","Acre","Amazonas","Roraima","Pará","Amapá","Tocantins","Maranhão","Piauí","Ceará",
                                        "Rio Grande do Norte","Paraíba","Pernambuco","Alagoas","Sergipe","Bahia",
                                        "Minas Gerais","Espírito Santo","Rio de Janeiro","São Paulo",
                                        "Paraná","Santa Catarina","Rio Grande do Sul", 
                                        "Mato Grosso do Sul","Mato Grosso","Goiás","Distrito Federal"))
summary(pns2013.1$Unidades_da_Federacao)

Rondônia                Acre            Amazonas             Roraima 
               1694                1814                2586                1591 
               Pará               Amapá           Tocantins            Maranhão 
               2004                1332                1515                1774 
              Piauí               Ceará Rio Grande do Norte             Paraíba 
               1804                2560                1691                1943 
         Pernambuco             Alagoas             Sergipe               Bahia 
               2591                1748                1553                2641 
       Minas Gerais      Espírito Santo      Rio de Janeiro           São Paulo 
               3779                1724                3486                5305 
             Paraná      Santa Catarina   Rio Grande do Sul  Mato Grosso do Sul 
               3012                1623                2913                1809 
        Mato Grosso               Goiás    Distrito Federal 
               1476                2423                1811

### Grandes Regiões

In [185]:
#Grandes Regiões
pns2013.1 <- pns2013.1 %>% 
  mutate(GrandesRegioes = fct_collapse(Unidades_da_Federacao, 
                                          `Norte` = c("Rondônia","Acre","Amazonas","Roraima","Pará", "Amapá","Tocantins"),
                                          `Nordeste` = c("Maranhão", "Piauí", "Ceará", "Rio Grande do Norte", "Paraíba","Pernambuco", "Alagoas","Sergipe","Bahia"),
                                          `Sudeste` = c("Minas Gerais", "Espírito Santo","Rio de Janeiro", "São Paulo"), 
                                          `Sul` = c("Paraná", "Santa Catarina", "Rio Grande do Sul"),
                                          `Centro-Oeste`= c("Mato Grosso do Sul","Mato Grosso", "Goiás", "Distrito Federal")))
summary(pns2013.1$GrandesRegioes)

Norte     Nordeste      Sudeste          Sul Centro-Oeste 
       12536        18305        14294         7548         7519

### Capital

In [186]:
#Capital
pns2013.1<- pns2013.1 %>% mutate(Capital= fct_collapse(Unidades_da_Federacao,
                                        `Porto Velho`= "Rondônia", 
                                        `Boa Vista`= "Roraima",              
                                        `Rio Branco`= "Acre", 
                                        `Manaus` = "Amazonas",
                                        `Belém` = "Pará" ,
                                        `Macapá`= "Amapá",
                                        `Palmas` = "Tocantins",
                                        `São Luís` = "Maranhão",
                                        `Teresina`= "Piauí" ,
                                        `Fortaleza`= "Ceará",
                                        `Natal`= "Rio Grande do Norte",
                                        `João Pessoa`= "Paraíba",
                                        `Recife`= "Pernambuco",
                                        `Maceió`= "Alagoas",
                                        `Aracaju`= "Sergipe",
                                        `Salvador`= "Bahia",
                                        `Belo Horizonte`= "Minas Gerais",
                                        `Vitória`= "Espírito Santo",
                                        `Rio de Janeiro`= "Rio de Janeiro",
                                        `São Paulo`= "São Paulo",
                                        `Curitiba`= "Paraná",
                                        `Florianópolis`= "Santa Catarina",
                                        `Porto Alegre`= "Rio Grande do Sul",
                                        `Campo Grande`=  "Mato Grosso do Sul",
                                        `Cuiabá`= "Mato Grosso",
                                        `Goiânia` = "Goiás",
                                        `Brasília`= "Distrito Federal"))
summary(pns2013.1$Capital)

Porto Velho     Rio Branco         Manaus      Boa Vista          Belém 
          1694           1814           2586           1591           2004 
        Macapá         Palmas       São Luís       Teresina      Fortaleza 
          1332           1515           1774           1804           2560 
         Natal    João Pessoa         Recife         Maceió        Aracaju 
          1691           1943           2591           1748           1553 
      Salvador Belo Horizonte        Vitória Rio de Janeiro      São Paulo 
          2641           3779           1724           3486           5305 
      Curitiba  Florianópolis   Porto Alegre   Campo Grande         Cuiabá 
          3012           1623           2913           1809           1476 
       Goiânia       Brasília 
          2423           1811

### Faixa Etária

In [187]:
#Faixas Etárias
pns2013.1 <-  pns2013.1 %>% mutate(faixa_idade=cut(C008,
  breaks = c(18,30, 45, 60, 75,Inf),
  labels = c("18 a 29 anos","30 a 44 anos","45 a 59 anos","60 a 74 anos","75 anos ou mais"), 
  ordered_result = TRUE, right = FALSE))
summary(pns2013.1$faixa_idade) 

18 a 29 anos    30 a 44 anos    45 a 59 anos    60 a 74 anos 75 anos ou mais 
          14321           20242           14462            8290            2887

### Raça

In [188]:
#Raça
pns2013.1 <- pns2013.1 %>% mutate(Raca= ifelse(C009==1, 1, 
                                        ifelse(C009==2, 2, 
                                        ifelse(C009==4, 3, 9))))

pns2013.1$Raca<-factor(pns2013.1$Raca, levels=c(1,2,3),labels=c("Branca", "Preta", "Parda"))

summary(pns2013.1$Raca)

Branca  Preta  Parda   NA's 
 24106   5631  29512    953

### Renda per capita

In [189]:
#Rendimento domiciliar per capita
pns2013.1 <-  pns2013.1  %>% mutate(rend_per_capita=cut(VDF003,
  breaks = c(-Inf,339, 678, 1356, 2034,Inf),
  labels=c("Até 1/2 SM","1/2 até 1 SM","1 até 2 SM","2 até 3 SM","Mais de 3 SM"), 
  ordered_result = TRUE, right = TRUE, na.exclude= TRUE))

summary(pns2013.1$rend_per_capita)

Até 1/2 SM 1/2 até 1 SM   1 até 2 SM   2 até 3 SM Mais de 3 SM         NA's 
       14256        17504        15493         5335         7603           11

### Escolaridade

In [190]:
# Escolaridade
pns2013.1 <- pns2013.1 %>% mutate(gescol = ifelse(VDD004A %in% 1:2, 1, 
                        ifelse(VDD004A%in% 3:4, 2, 
                        ifelse(VDD004A%in% 5:6, 3,4
                        ))))

pns2013.1$gescol<-factor(pns2013.1$gescol, levels=c(1,2,3,4), 
                                   labels=c("Fundamental incompleto ou equivalente","Médio incompleto ou equivalente",
                                           "Superior incompleto ou equivalente","Superior completo"))
summary(pns2013.1$gescol)

Fundamental incompleto ou equivalente       Médio incompleto ou equivalente 
                                24083                                  9215 
   Superior incompleto ou equivalente                     Superior completo 
                                19149                                  7755

## Criando indicadores

### Filtrando base de indicadores

In [191]:
#Selecionando variáveis para cálculo de indicadores no survey
pns2013Usurvey<- pns2013.1 %>% select("V0024","UPA_PNS","peso_morador_selec", "U001P","U002P","U003P","U004P","U005P","U006P",
                                     "C008","C009","V0031","Sit_Urbano_Rural","Sexo","Unidades_da_Federacao", "GrandesRegioes",
                                     "faixa_idade", "Raca","rend_per_capita","gescol","Capital")
summary(pns2013Usurvey)

     V0024            UPA_PNS        peso_morador_selec  U001P      
 Min.   :1110011   Min.   :1100001   Min.   : 0.004156   Sim:53594  
 1st Qu.:2210013   1st Qu.:2200075   1st Qu.: 0.243959   Não: 6608  
 Median :2951023   Median :2900192   Median : 0.521557              
 Mean   :3035353   Mean   :3007819   Mean   : 1.000000              
 3rd Qu.:4110111   3rd Qu.:4100002   3rd Qu.: 1.147413              
 Max.   :5310220   Max.   :5300180   Max.   :31.179597              
                                                                    
 U002P       U003P       U004P       U005P        U006P            C008       
 Sim:30685   Sim:39572   Sim: 6606   Sim:14271   Sim : 6451   Min.   : 18.00  
 Não:29517   Não:20630   Não:53596   Não:45931   Não :19205   1st Qu.: 30.00  
                                                 NA's:34546   Median : 41.00  
                                                              Mean   : 43.31  
                                                     

### Exporta tabela filtrada com os dados específicos - Módulo U 2013

In [192]:
#Salvando csv para cálculo de indicadores no survey
diretorio_saida <- "<coloque aqui o diretório>"
write.csv(pns2013Usurvey, file.path(diretorio_saida, "pns2013Usurvey.csv"))

### Cria plano amostral complexo

In [193]:
#survey design
desPNSU=svydesign(id=~UPA_PNS, strat=~V0024, weight=~peso_morador_selec, nest=TRUE, data=pns2013Usurvey)
desPNSU18=subset(desPNSU, C008>=18)
desPNSUC18=subset(desPNSU, C008>=18 & V0031==1)
desPNSUR18=subset(desPNSU, C008>=18 & C009!=9)

In [194]:
#survey design -U006P
desPNSU006P_18=subset(desPNSU, C008>=18 & !is.na(U006P))
desPNSU006P_R18=subset(desPNSU, C008>=18 & !is.na(U006P) & C009!=9)
desPNSU006P_C18=subset(desPNSU, C008>=18 & V0031==1 & !is.na(U006P))

### Criação da tabela de indicadores
Essa tabela é responsável por unir os indicadores no formato do painel de indicadores

In [195]:
matrizIndicadores = data.frame()

#### Definição de variáveis para iteração dos indicadores

In [196]:
ListaIndicadores = c(~U001P,~U002P,~U003P,~U004P,~U005P,~U006P)
ListaIndicadoresTexto = c("U001P","U002P","U003P","U004P","U005P","U006P")
ListaDominios = c(~Sexo,~Raca,~rend_per_capita,~faixa_idade,~Sit_Urbano_Rural,~Unidades_da_Federacao,~GrandesRegioes,~gescol,~Capital)
ListaDominiosTexto = c("sexo","raça","rend_per_capita","fx_idade_18","urb_rur","uf","região","gescol","capital")
ListaTotais = c('Brasil','Capital')
Ano <- "2013"

#### Preenchendo a tabela de indicadores
Essas iterações rodam por indicador, abrangência e por design

In [197]:
#Cálculo dos indicadores usando o pacote survey 
i <- 0
#Para cada indicador
for( indicador in ListaIndicadores){
    i <- i + 1
    j <- 1
    #Para cada dominio
    for (dominio in ListaDominios){
               #design especifico para capital que é subconjunto do dataframe total
               if (ListaDominiosTexto[j]=="capital"){
                   #designs especificos por variavel que são subconjuntos do dataset total
                   if(ListaIndicadoresTexto[i] == "U006P"){
                     dataframe_indicador<-svyby( indicador , dominio , desPNSU006P_C18 , svymean,vartype= c("ci","cv"))
                   }else{dataframe_indicador<-svyby( indicador , dominio , desPNSUC18 , svymean,vartype= c("ci","cv"))
                   }
               #Uso design do subconjunto para raça/cor que inclui preta,branca e parda as outras 
               #não possuiam dados suficientes para os dominios dos indicadores
               }else if (ListaDominiosTexto[j]=="raça"){
                   if(ListaIndicadoresTexto[i] == "U006P"){
                           dataframe_indicador<-svyby( indicador , dominio , desPNSU006P_R18 , svymean,vartype= c("ci","cv"))
                   }else{dataframe_indicador<-svyby( indicador , dominio , desPNSUR18 , svymean,vartype= c("ci","cv"))
                   }
               #design geral para o subconjunto maior que 18 anos    
               }else {
                   if(ListaIndicadoresTexto[i] == "U006P"){
                           dataframe_indicador<-svyby( indicador , dominio , desPNSU006P_18 , svymean,vartype= c("ci","cv"))
                   }else{dataframe_indicador<-svyby( indicador , dominio , desPNSU18 , svymean,vartype=c("ci","cv"))
                   }
               }
               #União do dataframe de indicadores no formato do painel disponibilizado para PNS
               
               dataframe_indicador<-data.frame(dataframe_indicador)
               
               colnames(dataframe_indicador) <- c("abr_nome","Sim","Nao","LowerS","LowerN","UpperS","UpperN","cvS","cvN")
               dataframe_indicador$Indicador <- ListaIndicadoresTexto[i]
               dataframe_indicador$abr_tipo <- ListaDominiosTexto[j]
               dataframe_indicador$Ano <- Ano
               dataframe_indicador <- dataframe_indicador %>% select("abr_tipo","abr_nome","Ano","Indicador","Sim","LowerS","UpperS","cvS")
               matrizIndicadores <-rbind(matrizIndicadores,dataframe_indicador)
               j <- j + 1
               
    }
}

#### Criando a tabela pela abrangência total

In [198]:
matriz_totais <- data.frame()

#### Preenchendo a tabela com as abrangencia Brasil e total das capitais

In [199]:
i=0
#para cada indicador
for(indicador in ListaIndicadores){
    i <- i+1
    #para os totais Brasil e total das capitais
    for(total in ListaTotais){
        dataframe_indicador <- data.frame()
        dataframe_indicador_S <- data.frame()
        #Uso do design que é subconjunto do dataset para cada Capital
        if (total == "Capital"){
                   #Indicadores que são subconjunto do dataset tot
                   if(ListaIndicadoresTexto[i] == "U006P"){
                           dataframe_indicador <- svymean(indicador,desPNSU006P_C18)
                   }else{dataframe_indicador <- svymean(indicador,desPNSUC18)
                   }
                   
        } else {
                   if(ListaIndicadoresTexto[i] == "U006P"){
                           dataframe_indicador <- svymean(indicador,desPNSU006P_18)
                   }else{dataframe_indicador <- svymean(indicador,desPNSU18)
                   }
        }
      
       intervalo_confianca <- confint(dataframe_indicador)
        coeficiente_variacao <- cv(dataframe_indicador)
        dataframe_indicador <- cbind(data.frame(dataframe_indicador),data.frame(intervalo_confianca))
        dataframe_indicador <- cbind(data.frame(dataframe_indicador),data.frame(coeficiente_variacao))

        dataframe_indicador <- dataframe_indicador %>% 
                               select('mean','X2.5..','X97.5..',coeficiente_variacao) 
        
        dataframe_indicador <- dataframe_indicador %>% 
                                 slice(1)
        colnames(dataframe_indicador) <- c('Sim','LowerS','UpperS','cvS')
        dataframe_indicador <- dataframe_indicador %>% 
                               select('Sim','LowerS','UpperS','cvS')
        dataframe_indicador$Indicador <- ListaIndicadoresTexto[i]
        dataframe_indicador$abr_tipo <- "total"
        dataframe_indicador$abr_nome <- total
        dataframe_indicador$Ano <- Ano 
        dataframe_indicador <- dataframe_indicador %>% 
                             select("abr_tipo","abr_nome","Ano","Indicador",'Sim','LowerS','UpperS','cvS')
       
        matriz_totais <-rbind(matriz_totais,dataframe_indicador)
        
    }
}


#### Unindo tabela de indicadores e de totais

In [200]:
matrizIndicadores<-rbind(matrizIndicadores,matriz_totais)

#### Visualizando tabela de indicadores

In [201]:
matrizIndicadores

abr_tipo        abr_nome            Ano  Indicador
Masculino           sexo            Masculino           2013 U001P    
Feminino            sexo            Feminino            2013 U001P    
Branca              raça            Branca              2013 U001P    
Preta               raça            Preta               2013 U001P    
Parda               raça            Parda               2013 U001P    
Até 1/2 SM          rend_per_capita Até 1/2 SM          2013 U001P    
1/2 até 1 SM        rend_per_capita 1/2 até 1 SM        2013 U001P    
1 até 2 SM          rend_per_capita 1 até 2 SM          2013 U001P    
2 até 3 SM          rend_per_capita 2 até 3 SM          2013 U001P    
Mais de 3 SM        rend_per_capita Mais de 3 SM        2013 U001P    
18 a 29 anos        fx_idade_18     18 a 29 anos        2013 U001P    
30 a 44 anos        fx_idade_18     30 a 44 anos        2013 U001P    
45 a 59 anos        fx_idade_18     45 a 59 anos        2013 U001P    
60 a 74 anos        fx_idade_18     60 a 74 anos        2013 U001P    
75 anos ou mais     fx_idade_18     75 anos ou mais     2013 U001P    
urbano              urb_rur         urbano              2013 U001P    
rural               urb_rur         rural               2013 U001P    
Rondônia            uf              Rondônia            2013 U001P    
Acre                uf              Acre                2013 U001P    
Amazonas            uf              Amazonas            2013 U001P    
Roraima             uf              Roraima             2013 U001P    
Pará                uf              Pará                2013 U001P    
Amapá               uf              Amapá               2013 U001P    
Tocantins           uf              Tocantins           2013 U001P    
Maranhão            uf              Maranhão            2013 U001P    
Piauí               uf              Piauí               2013 U001P    
Ceará               uf              Ceará               2013 U001P    
Rio Grande do Norte uf              Rio Grande do Norte 2013 U001P    
Paraíba             uf              Paraíba             2013 U001P    
Pernambuco          uf              Pernambuco          2013 U001P    
⋮                   ⋮               ⋮                   ⋮    ⋮        
Fortaleza5          capital         Fortaleza           2013 U006P    
Natal5              capital         Natal               2013 U006P    
João Pessoa5        capital         João Pessoa         2013 U006P    
Recife5             capital         Recife              2013 U006P    
Maceió5             capital         Maceió              2013 U006P    
Aracaju5            capital         Aracaju             2013 U006P    
Salvador5           capital         Salvador            2013 U006P    
Belo Horizonte5     capital         Belo Horizonte      2013 U006P    
Vitória5            capital         Vitória             2013 U006P    
Rio de Janeiro11    capital         Rio de Janeiro      2013 U006P    
São Paulo10         capital         São Paulo           2013 U006P    
Curitiba5           capital         Curitiba            2013 U006P    
Florianópolis5      capital         Florianópolis       2013 U006P    
Porto Alegre5       capital         Porto Alegre        2013 U006P    
Campo Grande5       capital         Campo Grande        2013 U006P    
Cuiabá5             capital         Cuiabá              2013 U006P    
Goiânia5            capital         Goiânia             2013 U006P    
Brasília5           capital         Brasília            2013 U006P    
U001PSim            total           Brasil              2013 U001P    
U001PSim1           total           Capital             2013 U001P    
U002PSim            total           Brasil              2013 U002P    
U002PSim1           total           Capital             2013 U002P    
U003PSim            total           Brasil              2013 U003P    
U003PSim1           total           Capital             2013 U003P    
U004PSim            total           Brasil  

#### Exportando tabela de indicadores calculados - Módulo U 2013

In [202]:
diretorio_saida <- "<coloque aqui o diretório>"
write.table(matrizIndicadores,file=paste0(diretorio_saida,"Indicadores_2013U_R.csv"),sep = ";",dec = ",",row.names = FALSE)